# This notebook includes data analysis workflow to produce figures presented in 'The nanoscale ordering of cellulose in a hierarchically structured hybrid material revealed using scanning electron diffraction' paper and is written by Mathias Nero, MMK, Stockholm University

## 1. Load essential libraries

In [ ]:
%matplotlib inline

In [ ]:
import hyperspy.api as hs
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec
from skimage import feature

## 2. Load and pre-process the data

In [ ]:
dp = hs.load('SED_1c.hdf5')
dp

In [ ]:
#Convert the dataset into np array form for indexing in the next steps
# NOTE this transposes the navigation dimensions, x=y and y=x
dp2 = np.array(dp)
dp2.shape

In [ ]:
#find center of DP

aveDP = np.average(dp2, axis=(0,1))
blob=feature.blob_log(aveDP, min_sigma=6, max_sigma=10, threshold=200) #use scikit tool

fig, ax = plt.subplots()
ax.imshow(aveDP, cmap='gist_gray',vmin=0, vmax=400000)
ax.scatter(blob[:,1], blob[:,0])
plt.show()

ic=blob[:,0]
jc=blob[:,1]

print("ic (y) is " + str(ic))
print("jc (x) is " + str(jc))

## 3. Calculate the intensities at different rotation angles

In [ ]:
# Define the number of data points (angles) to be meaasured in the orbit around the direct beam
# this will define the step resolution, for example, here the number of angles are 360 so a step of 
# 1 degrees will be taken between each angular position in an orbit of 360 degrees
# Number of data points starts and ends at the same spot, that is why one extra is (361) needed
n_dots = 361  # set number of dots.
# 0 degrees is erased later. This is to separate no-signal from 180 degrees
angs = np.linspace(0, 2*np.pi, n_dots) # converto angles
cx, cy = (ic, jc)  # center of circle (y,x)
ra = 61 #put the value of 200-diffraction radius in pixels

In [ ]:
#initalize dot vectors
xs=[]
ys=[]

for ang in angs:     # compute (x,y) for each point
    x = cx + ra*np.cos(ang) # (ang) = start position at 6 o'clock
    y = cy + ra*np.sin(ang) #(ang+np.pi/2) changes the 'start' position from 6 to 3 o'clock
    xs.append(x)   # collect x
    ys.append(y)   # collect y

#convert xs and yx to integer numpy array, so values can be used for indexing
xs=np.asarray(xs).astype(int)
ys=np.asarray(ys).astype(int)


#initialize intensity vector, this vector contains the measured intensity values at each angular position
zi=np.zeros((1,len(angs)))

#Create a list vector which will compile the intensity vectors 'zi' from all the DPs  in the dataset
zi_list = np.zeros(1)
zi_list = zi_list.tolist()

In [ ]:
#Calculate the intensity vector for each DP and put in the list vector
#The number '+-5' here indicate the radie of the circular ring that will integrate the intensity values, 
#choose an optimum value here
for i in range(174): #rows
    for j in range(196): #columns
        for ii in range(0,len(angs)):
            testDP = dp2[i,j,:,:]
            zi[0, ii] = np.average(testDP[xs[ii][0]-5:xs[ii][0]+5, ys[ii][0]-5:ys[ii][0]+5])
        zi2 = zi.tolist()
        zi_list += zi2

## 4. Visualize the rotational intensity map

In [ ]:
# Define a 2D map area equivalent to the navigation dimentions for the rotation visualization map
Figure_3c = hs.signals.Signal2D(np.zeros((174,196))) #(rows, columns)
Figure_3c

In [ ]:
# For each dp, extract the intensity vector, calculate the angle(index) at the peak position
# and put the calculated angle back into the 2D map area defined above
# Define a threshold value (diffraction max/diffraction median)>dev
dev=1.5
for i in range(174):
    for j in range(196):
        k = (i*196) + (j+1)
        zi_array = np.multiply(zi_list[k][1:181], zi_list[k][181:])  # Multiply the two semicircles for better S/N, 0 degrees left out, using 360 instead
        if (max(zi_array)/np.median(zi_array)) > dev : 
            Figure_3c.isig[j,i] = np.argmax(zi_array) # Detector position now equals number of degrees
        else:
            Figure_3c.isig[j,i]= 0 # 0 is now 'no-signal', NOT 0 degrees

In [ ]:
# To make all zeros (below the threshold value) black using new 'hsv' cmap
import matplotlib as mpl
cmap = mpl.colormaps['hsv'].copy()
cmap.set_under(color='black')

In [ ]:
# Plot with Matplotlib and add colorwheel
color_wheel = hs.load('colorwheel-hsv.tif')
color_wheel.change_dtype('uint8')

fig, ax = plt.subplots()
ax.imshow(Figure_3c , cmap=cmap, vmin=0.1)
ax.imshow(color_wheel, extent=[200,240,170,130])
ax.set_title('Figure 3c')
ax.set_xlim(0, 250)
ax.set_ylim(174, 0)
ax.set_axis_off()